# Is it worth the time, at work?

There's a lovely XKCD comic, [Is It Worth the Time?](https://xkcd.com/1205/):

![comic](https://imgs.xkcd.com/comics/is_it_worth_the_time.png)

<br>

However, as pointed out in [this forum thread](http://forums.xkcd.com/viewtopic.php?t=101756#p3340931), there are a bunch of assumptions going into the chart that are not necessarily true:

> Great table, but I have to disagree with the numbers:
> 
> It seems like the calculation assumes 24-hour days and 365-day years, so the conversion from time saved t and frequency of task f to time worth spending T is
> 
> T = t \* f \* 5 years
> 
> with the straight unit conversion
> 
> 1 year = 365 days  
> 1 week = 7 days  
> 1 day = 24 hours
> 
> etc. However, most people don't work 24 hours/day, either when they are doing the repetitive task or when they are working to streamline it. So the conversions depend on what you consider a full day. If you consider your waking time, then the conversions should be more like
> 
> 1 year = 365 days  
> 1 week = 7 days  
> 1 day = 16 hours
> 
> If you want to use this chart for work, then the conversions should be more like
> 
> 1 year = 250 days  
> 1 week = 5 days  
> 1 day = 8 hours
> 
> in which case the chart looks quite different. For example, for a 1-hour task done weekly, one should invest 16 days (if considering waking hours) or 1 month (if considering working hours), rather than the 10 days indicated by the chart.

I'd like to use the chart for work.

Let's first replicate XKCD's chart, then update it with conversion assumptions more appropriate for work.

## Some Tools

Let's first define units. We use the units library natu.

In [1]:
from natu.units import s

# Traditional timespan definitions.
minute = 60 * s
hour   = 60 * minute
day    = 24 * hour
week   = 7  * day
month  = 30 * day
year   = 365 * day

# Work timespans.
work_day  = 8 * hour
work_week = 5 * work_day
work_year = 250 * work_day

Let's also put together some utilities to display our table of times nicely.

In [2]:
class ListTable(list):
    """
    Lovely table formatting snippet.
    via http://calebmadrigal.com/display-list-as-table-in-ipython-notebook/
    """
    def _repr_html_(self):
        html = ['<table style="margin: 10px auto">']
        for row in self:
            html.append("<tr>")
            for col in row:
                html.append("<td>{0}</td>".format(col))
            html.append("</tr>")
        html.append("</table>")
        return ''.join(html)

def display_time(time, display_units):
    "Converts a natu time to a string, using units from `display_units`."
    for unit, suffix in display_units:
        if time / unit >= 1.0:
            return u'{:.1f} {}'.format(time / unit, suffix)
    
    return u'{:.1f} seconds'.format(time / s)

# These hierarchies are used to convert into the most appropriate
# units with `display_time`.
xkcd_display_units = [
    (year, 'years'),
    (month, 'months'),
    (week, 'weeks'),
    (day, 'days'),
    (hour, 'hours'),
    (minute, 'minutes'),
]

work_display_units = [
    (work_year, 'work years'),
    (work_week, 'work weeks'),
    (work_day, 'work days'),
    (hour, 'hours'),
    (minute, 'minutes'),
]

Now, let's build a function to actually calculate the table.

In [3]:
def worth_it_table(frequency, time_saved, amortized_over, display_units):
    "Calculuate a 'Worth It?' table."
    def display(time):
        return display_time(time, display_units)

    table = ListTable()
    table.append([' ', '50/day', '5/day', '1/day', '1/week', '12/year', '1/year'])
    for t in time_saved:
        row = [
            display(amortized_over * t * f) if t * f < 1.0 else ''
            for f in frequency
        ]
        table.append([display(t)] + row)
    return table

## Verify Our Solution

Let's verify that it works with the original parameters.

In [4]:
# XKCD's "How often?" to row and "Time shaved" left column:
xkcd_frequency  = [50/day, 5/day, 1/day, 1/week, 12/year, 1/year]
xkcd_time_saved = [1*s, 5*s, 30*s, 1*minute, 5*minute, 30*minute, 1*hour, 6*hour, 1*day]

# XKCD amortizes it over 5 year.
worth_it_table(xkcd_frequency, xkcd_time_saved, 5 * year, xkcd_display_units)

[[' ', '50/day', '5/day', '1/day', '1/week', '12/year', '1/year'],
 [u'1.0 seconds',
  u'1.1 days',
  u'2.5 hours',
  u'30.4 minutes',
  u'4.3 minutes',
  u'1.0 minutes',
  u'5.0 seconds'],
 [u'5.0 seconds',
  u'5.3 days',
  u'12.7 hours',
  u'2.5 hours',
  u'21.7 minutes',
  u'5.0 minutes',
  u'25.0 seconds'],
 [u'30.0 seconds',
  u'1.1 months',
  u'3.2 days',
  u'15.2 hours',
  u'2.2 hours',
  u'30.0 minutes',
  u'2.5 minutes'],
 [u'1.0 minutes',
  u'2.1 months',
  u'6.3 days',
  u'1.3 days',
  u'4.3 hours',
  u'1.0 hours',
  u'5.0 minutes'],
 [u'5.0 minutes',
  u'10.6 months',
  u'1.1 months',
  u'6.3 days',
  u'21.7 hours',
  u'5.0 hours',
  u'25.0 minutes'],
 [u'30.0 minutes',
  '',
  u'6.3 months',
  u'1.3 months',
  u'5.4 days',
  u'1.2 days',
  u'2.5 hours'],
 [u'1.0 hours',
  '',
  u'1.0 years',
  u'2.5 months',
  u'1.6 weeks',
  u'2.5 days',
  u'5.0 hours'],
 [u'6.0 hours',
  '',
  '',
  u'1.2 years',
  u'2.2 months',
  u'2.1 weeks',
  u'1.2 days'],
 [u'1.0 days', '', '', '', u'8.7 months', u'2.0 months', u'5.0 days']]

Take a look at the original comic and compare:

![comic](https://imgs.xkcd.com/comics/is_it_worth_the_time.png)

<br>

Looks good to me!

## Is it worth the time, at work?

Now let's try it with "work" definitions of time spans, and amortize over only 1 year.

In [5]:
work_frequency  = [50/work_day, 5/work_day, 1/work_day, 1/work_week, 12/work_year, 1/work_year]
work_time_saved = [1*s, 5*s, 30*s, 1*minute, 5*minute, 30*minute, 1*hour, 6*hour, 1*work_day]

worth_it_table(work_frequency, work_time_saved, 1 * work_year, work_display_units)

[[' ', '50/day', '5/day', '1/day', '1/week', '12/year', '1/year'],
 [u'1.0 seconds',
  u'3.5 hours',
  u'20.8 minutes',
  u'4.2 minutes',
  u'50.0 seconds',
  u'12.0 seconds',
  u'1.0 seconds'],
 [u'5.0 seconds',
  u'2.2 work days',
  u'1.7 hours',
  u'20.8 minutes',
  u'4.2 minutes',
  u'1.0 minutes',
  u'5.0 seconds'],
 [u'30.0 seconds',
  u'2.6 work weeks',
  u'1.3 work days',
  u'2.1 hours',
  u'25.0 minutes',
  u'6.0 minutes',
  u'30.0 seconds'],
 [u'1.0 minutes',
  u'5.2 work weeks',
  u'2.6 work days',
  u'4.2 hours',
  u'50.0 minutes',
  u'12.0 minutes',
  u'60.0 seconds'],
 [u'5.0 minutes',
  u'26.0 work weeks',
  u'2.6 work weeks',
  u'2.6 work days',
  u'4.2 hours',
  u'1.0 hours',
  u'5.0 minutes'],
 [u'30.0 minutes',
  '',
  u'15.6 work weeks',
  u'3.1 work weeks',
  u'3.1 work days',
  u'6.0 hours',
  u'30.0 minutes'],
 [u'1.0 hours',
  '',
  u'31.2 work weeks',
  u'6.2 work weeks',
  u'1.2 work weeks',
  u'1.5 work days',
  u'60.0 minutes'],
 [u'6.0 hours',
  '',
  '',
  u'37.5 work weeks',
  u'7.5 work weeks',
  u'1.8 work weeks',
  u'6.0 hours'],
 [u'1.0 work days',
  '',
  '',
  '',
  u'10.0 work weeks',
  u'2.4 work weeks',
  u'8.0 hours']]

Interesting...

Now go forth and make productive decisions!

<br>